## Model Training

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline
import seaborn as sns

In [2]:
import warnings
warnings.filterwarnings('ignore')

In [3]:
pd.set_option('display.max_columns', None)

In [4]:
df = pd.read_csv("E:/VS_Code/Projects/Customer_Churn/notebooks/data/processed_customer_churn_data.csv")

df.sample(6)

customer_id  gender  age married  number_of_dependents           city  \
2633  3745-HRPHI    Male   49     Yes                     3      Yuba City   
3132  4489-SNOJF  Female   28     Yes                     2      Deer Park   
1589  2320-JRSDE  Female   33     Yes                     1      Richgrove   
6032  8544-GOQSH  Female   51      No                     0        Pacoima   
5086  7143-BQIBA    Male   32      No                     0       Petaluma   
6944  9847-HNVGP    Male   23      No                     0  Monterey Park   

      zip_code   latitude   longitude  number_of_referrals  tenure_in_months  \
2633     95993  39.075694 -121.706060                    0                66   
3132     94576  38.554383 -122.474773                    1                35   
1589     93261  35.809921 -119.127437                    1                 1   
6032     91331  34.255442 -118.421314                    0                14   
5086     94954  38.235021 -122.557332                    0                10   
6944     91755  34.049172 -118.115022                    0                17   

         offer phone_service  avg_monthly_long_distance_charges  \
2633  No Offer            No                                  0   
3132  No Offer           Yes                                 25   
1589  No Offer           Yes                                  7   
6032   Offer D           Yes                                  1   
5086   Offer D           Yes                                  7   
6944   Offer D           Yes                                 25   

     multiple_lines internet_service internet_type  avg_monthly_gb_download  \
2633             No              Yes           DSL                     28.0   
3132            Yes              Yes           DSL                     82.0   
1589             No               No   No Internet                      0.0   
6032             No              Yes   Fiber Optic                     21.0   
5086             No              Yes           DSL                     17.0   
6944             No               No   No Internet                      0.0   

     online_security online_backup device_protection_plan  \
2633              No            No                    Yes   
3132             Yes            No                    Yes   
1589              No            No                     No   
6032              No           Yes                     No   
5086             Yes            No                     No   
6944              No            No                     No   

     premium_tech_support streaming_tv streaming_movies streaming_music  \
2633                  Yes          Yes              Yes             Yes   
3132                  Yes          Yes               No              No   
1589                   No           No               No              No   
6032                  Yes           No               No              No   
5086                  Yes          Yes               No              No   
6944                   No           No               No              No   

     unlimited_data        contract paperless_billing   payment_method  \
2633            Yes        Two Year                No  Bank Withdrawal   
3132            Yes  Month-to-Month                No  Bank Withdrawal   
1589             No  Month-to-Month               Yes  Bank Withdrawal   
6032            Yes  Month-to-Month               Yes      Credit Card   
5086            Yes  Month-to-Month                No  Bank Withdrawal   
6944             No        One Year                No      Credit Card   

      monthly_charge  total_charges  total_refunds  total_extra_data_charges  \
2633           54.65        3632.00          46.75                         0   
3132           72.25        2568.55           0.00                         0   
1589           19.90          19.90           0.00                         0   
6032           80.05        1112.30           0.00                         0   


In [5]:
df.shape

(7043, 44)

#### **MODEL with Hyperparameter Tuning**

In [66]:
!pip install category_encoders

In [68]:
!pip install catboost

  Using cached graphviz-0.21-py3-none-any.whl.metadata (12 kB)
   ---------------------------------------- 0.0/102.4 MB ? eta -:--:--
   - -------------------------------------- 4.7/102.4 MB 22.4 MB/s eta 0:00:05
   --- ------------------------------------ 9.7/102.4 MB 25.6 MB/s eta 0:00:04
   ------- -------------------------------- 19.4/102.4 MB 31.0 MB/s eta 0:00:03
   ------------- -------------------------- 35.7/102.4 MB 43.9 MB/s eta 0:00:02
   ------------- -------------------------- 35.7/102.4 MB 43.9 MB/s eta 0:00:02
   ------------- -------------------------- 35.7/102.4 MB 43.9 MB/s eta 0:00:02
   ------------- -------------------------- 35.7/102.4 MB 43.9 MB/s eta 0:00:02
   -------------- ------------------------- 35.9/102.4 MB 21.0 MB/s eta 0:00:04
   --------------------- ------------------ 55.8/102.4 MB 29.0 MB/s eta 0:00:02
   ---------------------------- ----------- 73.1/102.4 MB 34.5 MB/s eta 0:00:01
   ------------------------------ --------- 78.6/102.4 MB 33.8 MB/s 

In [72]:
!pip install optuna

  Using cached sqlalchemy-2.0.41-cp313-cp313-win_amd64.whl.metadata (9.8 kB)
  Using cached tqdm-4.67.1-py3-none-any.whl.metadata (57 kB)
Using cached sqlalchemy-2.0.41-cp313-cp313-win_amd64.whl (2.1 MB)
Using cached tqdm-4.67.1-py3-none-any.whl (78 kB)

   ---------------------------------------- 0/7 [tqdm]
   ---------------------------------------- 0/7 [tqdm]
   ---------------------------------------- 0/7 [tqdm]
   ---------------------------------------- 0/7 [tqdm]
   ---------------------------------------- 0/7 [tqdm]
   ----- ---------------------------------- 1/7 [Mako]
   ----- ---------------------------------- 1/7 [Mako]
   ----- ---------------------------------- 1/7 [Mako]
   ----- ---------------------------------- 1/7 [Mako]
   ----------- ---------------------------- 2/7 [greenlet]
   ----------- ---------------------------- 2/7 [greenlet]
   ----------- ---------------------------- 2/7 [greenlet]
   ----------------- ---------------------- 3/7 [colorlog]
   -----------

In [5]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns

In [1]:
from sklearn.model_selection import train_test_split

from sklearn.compose import ColumnTransformer
from sklearn.pipeline import Pipeline

from sklearn.impute import SimpleImputer

from category_encoders import CatBoostEncoder
from category_encoders.target_encoder import TargetEncoder
from sklearn.preprocessing import OneHotEncoder

from sklearn.preprocessing import LabelEncoder

from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import StandardScaler

from sklearn.feature_selection import VarianceThreshold, SelectKBest, mutual_info_classif

In [3]:
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier, GradientBoostingClassifier
from sklearn.linear_model import LogisticRegression
from xgboost import XGBClassifier
from catboost import CatBoostClassifier
from lightgbm import LGBMClassifier
from sklearn.svm import SVC

from sklearn.model_selection import cross_val_score, StratifiedKFold, train_test_split, cross_validate

from sklearn.metrics import (
    roc_auc_score, accuracy_score, precision_score, 
    recall_score, f1_score, confusion_matrix, classification_report
)

In [4]:
import optuna
from optuna.visualization import plot_param_importances, plot_optimization_history
from optuna.exceptions import TrialPruned

import joblib

import sys
import os
from src.logger import logging

e:\VS_Code\Projects\Customer_Churn\venv\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [19]:
class AutoMLTrainer:
    def __init__(self, X, y, test_size=0.2, random_state=42):
        """
        Initialize AutoML Trainer
        
        Args:
            X: Features DataFrame
            y: Target Series
            test_size: Size of test split
            random_state: Random seed
        """
        self.X = X
        self.y = y
        self.test_size = test_size
        self.random_state = random_state
        
        # Prepare data
        self._prepare_data()
        
        # Initialize results storage
        self.results = []
        self.best_model = None
        self.best_model_name = None
        self.best_pipeline = None
        self.feature_importances = None
        
        # Configure components
        self._configure_components()
        
        logging.info("AutoML Trainer initialized successfully")

    def _prepare_data(self):
        """Prepare and validate data"""
        # Split data
        self.X_train, self.X_test, self.y_train, self.y_test = train_test_split(
            self.X, self.y, test_size=self.test_size, 
            stratify=self.y, random_state=self.random_state
        )
        
        # Identify feature types
        self.numerical_cols = self.X.select_dtypes(include=np.number).columns.tolist()
        self.categorical_cols = self.X.select_dtypes(exclude=np.number).columns.tolist()
        
        # Validate and encode target
        self._validate_target()
        
        # Validate features
        self._validate_features()
        
        logging.info(f"Data prepared. Train: {self.X_train.shape}, Test: {self.X_test.shape}")
        logging.info(f"Numerical features: {len(self.numerical_cols)}, Categorical features: {len(self.categorical_cols)}")

    def _validate_target(self):
        """Validate and encode target variable"""
        if self.y_train.dtype == 'object' or self.y_train.dtype.name == 'category':
            self.label_encoder = LabelEncoder()
            self.y_train = self.label_encoder.fit_transform(self.y_train)
            self.y_test = self.label_encoder.transform(self.y_test)
            logging.info("Encoded categorical target variable")
        
        # Check classification type
        self.n_classes = len(np.unique(self.y_train))
        self.problem_type = "binary" if self.n_classes == 2 else "multiclass"
        logging.info(f"{self.problem_type.capitalize()} classification task detected")

    def _validate_features(self):
        """Validate features and remove problematic columns"""
        # Remove constant features
        constant_cols = []
        for col in self.numerical_cols:
            if self.X_train[col].nunique() == 1:
                constant_cols.append(col)
        
        if constant_cols:
            logging.warning(f"Removing constant features: {constant_cols}")
            self.numerical_cols = [col for col in self.numerical_cols if col not in constant_cols]
        
        # Check for missing values
        self._check_missing_values()

    def _check_missing_values(self):
        """Check and log missing values"""
        missing_num = self.X_train[self.numerical_cols].isna().sum().sum()
        missing_cat = self.X_train[self.categorical_cols].isna().sum().sum()
        
        if missing_num or missing_cat:
            logging.warning(f"Missing values detected - Numerical: {missing_num}, Categorical: {missing_cat}")

    def _configure_components(self):
        """Configure encoders, scalers, and models"""
        # Preprocessing components (remain as before for 'none' to skip steps)
        self.encoders = {
            'onehot': OneHotEncoder(handle_unknown='ignore', sparse_output=False),
            'target': TargetEncoder(),
            'catboost': CatBoostEncoder()
        }

        self.scalers = {
            'standard': StandardScaler(),
            'minmax': MinMaxScaler(),
            'none': None
        }

        self.feature_selectors = {
            'variance': VarianceThreshold(threshold=0.01),
            'mutual_info': SelectKBest(score_func=mutual_info_classif, k='all'),
            'none': None
        }

        self.models = {
            'LogisticRegression': {
                'model': LogisticRegression,
                'params': lambda trial: {
                    'classifier__C': trial.suggest_float('C', 1e-3, 100, log=True),
                    'classifier__solver': trial.suggest_categorical('solver', ['lbfgs', 'saga', 'liblinear']),
                    'classifier__max_iter': 1000,
                    'classifier__class_weight': trial.suggest_categorical('class_weight', ['balanced', None]),
                    'classifier__n_jobs': -1 if trial.suggest_categorical('lr_n_jobs', [True, False]) else 1
                }
            },
            'RandomForest': {
                'model': RandomForestClassifier,
                'params': lambda trial: {
                    'classifier__n_estimators': trial.suggest_int('n_estimators', 100, 500),
                    'classifier__max_depth': trial.suggest_int('max_depth', 5, 20),
                    'classifier__min_samples_split': trial.suggest_int('min_samples_split', 2, 15),
                    'classifier__class_weight': trial.suggest_categorical('class_weight', ['balanced', 'balanced_subsample', None]),
                    'classifier__n_jobs': -1
                }
            },
            'SVM': {
                'model': SVC,
                'params': lambda trial: {
                    'classifier__C': trial.suggest_float('C', 1e-2, 100, log=True),
                    'classifier__kernel': trial.suggest_categorical('kernel', ['linear', 'rbf', 'poly']),
                    'classifier__gamma': trial.suggest_categorical('gamma', ['scale', 'auto']) if trial.suggest_categorical('gamma_choice', [True, False]) else trial.suggest_float('gamma_custom', 1e-4, 1e-1, log=True),
                    'classifier__degree': trial.suggest_int('degree', 2, 5) if trial.using_param('kernel', 'poly') else 3, # Only for 'poly' kernel
                    'classifier__class_weight': trial.suggest_categorical('class_weight', ['balanced', None]),
                    'classifier__probability': True,
                    'classifier__random_state': self.random_state
                }
            },
            'XGBoost': {
                'model': XGBClassifier,
                'params': lambda trial: {
                    'classifier__n_estimators': trial.suggest_int('n_estimators', 100, 1000), 
                    'classifier__learning_rate': trial.suggest_float('learning_rate', 0.01, 0.3, log=True), 
                    'classifier__max_depth': trial.suggest_int('max_depth', 3, 10), 
                    'classifier__subsample': trial.suggest_float('subsample', 0.6, 1.0), 
                    'classifier__colsample_bytree': trial.suggest_float('colsample_bytree', 0.6, 1.0), 
                    'classifier__reg_alpha': trial.suggest_float('reg_alpha', 1e-8, 1.0, log=True), 
                    'classifier__reg_lambda': trial.suggest_float('reg_lambda', 1e-8, 1.0, log=True), 
                    'classifier__gamma': trial.suggest_float('gamma', 1e-8, 1.0, log=True), 
                    'classifier__use_label_encoder': False, 
                    'classifier__eval_metric': 'logloss' if self.problem_type == "binary" else 'mlogloss', 
                    'classifier__objective': 'binary:logistic' if self.problem_type == "binary" else 'multi:softprob', 
                    'classifier__scale_pos_weight': trial.suggest_categorical('scale_pos_weight', [1, None]) if self.problem_type == "binary" else 1, 
                    'classifier__tree_method': 'hist',
                    'classifier__random_state': self.random_state
                }
            },
            'CatBoost': {
                'model': CatBoostClassifier,
                'params': lambda trial: {
                    'classifier__iterations': trial.suggest_int('iterations', 500, 1500), # Increased range
                    'classifier__learning_rate': trial.suggest_float('learning_rate', 0.01, 0.3, log=True),
                    'classifier__depth': trial.suggest_int('depth', 4, 10), # Increased depth
                    'classifier__l2_leaf_reg': trial.suggest_float('l2_leaf_reg', 1e-8, 10, log=True), # Broader L2 range
                    'classifier__min_data_in_leaf': trial.suggest_int('min_data_in_leaf', 1, 30), # Added
                    'classifier__auto_class_weights': trial.suggest_categorical('auto_class_weights', ['Balanced', 'SqrtBalanced', False]),
                    'classifier__loss_function': 'Logloss' if self.problem_type == "binary" else 'MultiClass', # Specify loss
                    'classifier__eval_metric': 'AUC' if self.problem_type == "binary" else 'MultiClassOneVsAll', # Specify eval metric
                    'classifier__verbose': False,
                    'classifier__task_type': 'CPU',
                    'classifier__random_seed': self.random_state
                }
            },
            'LightGBM': {
                'model': LGBMClassifier,
                'params': lambda trial: {
                    'classifier__n_estimators': trial.suggest_int('n_estimators', 100, 1000), # Increased range
                    'classifier__learning_rate': trial.suggest_float('learning_rate', 0.01, 0.3, log=True),
                    'classifier__num_leaves': trial.suggest_int('num_leaves', 20, 200), # Increased range
                    'classifier__max_depth': trial.suggest_int('max_depth', 3, 12), # Increased depth
                    'classifier__min_child_samples': trial.suggest_int('min_child_samples', 10, 80), # Broader range
                    'classifier__subsample': trial.suggest_float('subsample', 0.6, 1.0), # Added
                    'classifier__colsample_bytree': trial.suggest_float('colsample_bytree', 0.6, 1.0), # Added
                    'classifier__reg_alpha': trial.suggest_float('reg_alpha', 1e-8, 1.0, log=True), # L1 regularization
                    'classifier__reg_lambda': trial.suggest_float('reg_lambda', 1e-8, 1.0, log=True), # L2 regularization
                    'classifier__class_weight': trial.suggest_categorical('class_weight', ['balanced', None]),
                    'classifier__objective': 'binary' if self.problem_type == "binary" else 'multiclass', # Specify objective
                    'classifier__metric': 'auc' if self.problem_type == "binary" else 'multi_logloss', # Specify metric
                    'classifier__n_jobs': -1,
                    'classifier__random_state': self.random_state
                }
            }
        }

        logging.info("Components configured: %d encoders, %d scalers, %d feature selectors, %d models",
                     len(self.encoders), len(self.scalers), len(self.feature_selectors), len(self.models))
        
    def create_pipeline(self, encoder_name, scaler_name, selector_name, model_name):
        """
        Create robust pipeline with feature selection
        
        Args:
            encoder_name: Name of categorical encoder
            scaler_name: Name of numerical scaler
            selector_name: Name of feature selector
            model_name: Name of model
            
        Returns:
            Configured pipeline
        """
        # Numerical pipeline
        num_steps = [('imputer', SimpleImputer(strategy='median'))]
        
        if scaler_name != 'none':
            num_steps.append(('scaler', self.scalers[scaler_name]))
            
        num_pipeline = Pipeline(num_steps)
        
        # Categorical pipeline
        cat_pipeline = Pipeline([
            ('imputer', SimpleImputer(strategy='most_frequent')),
            ('encoder', self.encoders[encoder_name])
        ])
        
        # Preprocessor
        preprocessor = ColumnTransformer([
            ('num', num_pipeline, self.numerical_cols),
            ('cat', cat_pipeline, self.categorical_cols)
        ])
        
        # Main pipeline
        pipeline_steps = [('preprocessor', preprocessor)]
        
        # Feature selection
        if selector_name != 'none':
            pipeline_steps.append(('feature_selector', self.feature_selectors[selector_name]))
        
        # Model
        pipeline_steps.append(('classifier', self.models[model_name]['model']()))
        
        return Pipeline(pipeline_steps)

    def objective(self, trial, encoder_name, scaler_name, selector_name, model_name):
        """
        Objective function for Optuna optimization
        
        Args:
            trial: Optuna trial object
            encoder_name: Encoder to use
            scaler_name: Scaler to use
            selector_name: Feature selector to use
            model_name: Model to use
            
        Returns:
            Mean CV score
        """
        try:
            # Create pipeline
            pipeline = self.create_pipeline(encoder_name, scaler_name, selector_name, model_name)
            
            # Set hyperparameters
            params = self.models[model_name]['params'](trial)
            pipeline.set_params(**params)
            
            # Manual cross-validation with error handling
            cv = StratifiedKFold(n_splits=3, shuffle=True, random_state=self.random_state)
            scores = []
            
            for fold, (train_idx, val_idx) in enumerate(cv.split(self.X_train, self.y_train)):
                try:
                    # Train on fold
                    X_fold_train = self.X_train.iloc[train_idx]
                    y_fold_train = self.y_train.iloc[train_idx]
                    pipeline.fit(X_fold_train, y_fold_train)
                    
                    # Validate on fold
                    X_val = self.X_train.iloc[val_idx]
                    y_val = self.y_train.iloc[val_idx]
                    
                    # Calculate score
                    if hasattr(pipeline.named_steps['classifier'], 'predict_proba'):
                        y_proba = pipeline.predict_proba(X_val)
                        score = roc_auc_score(y_val, y_proba[:, 1] if self.problem_type == "binary" else y_proba, 
                                              multi_class='ovr' if self.problem_type == "multiclass" else 'raise')
                    else:
                        y_pred = pipeline.predict(X_val)
                        score = roc_auc_score(y_val, y_pred)
                    
                    scores.append(score)
                    logging.debug(f"Fold {fold+1}: {model_name} AUC = {score:.4f}")
                    
                except Exception as e:
                    logging.warning(f"Fold {fold+1} failed: {str(e)}")
                    scores.append(0.5)  # Neutral score for failed fold
            
            # Calculate mean score
            mean_score = np.mean(scores)
            logging.info(f"{model_name} Mean AUC: {mean_score:.4f}")
            return mean_score
        
        except Exception as e:
            logging.error(f"Objective failed: {str(e)}")
            return float('-inf')

    def optimize(self, n_trials=20, timeout=600):
        """
        Optimize model with feature selection
        
        Args:
            n_trials: Number of trials per configuration
            timeout: Timeout per configuration in seconds
        """
        
        self.results = []
        
        # Dynamically generate all possible configurations
        all_encoders = self.encoders.keys()
        all_scalers = self.scalers.keys()
        all_selectors = self.feature_selectors.keys()
        all_models = self.models.keys()

        configurations = []
        for encoder_name in all_encoders:
            for scaler_name in all_scalers:
                for selector_name in all_selectors:
                    for model_name in all_models:
                        configurations.append((encoder_name, scaler_name, selector_name, model_name))

        # IMPORTANT: This will create a very large number of configurations!
        # Consider a smaller subset for initial testing, or implement a more
        # sophisticated search strategy (e.g., genetic algorithms, multi-objective optimization)
        # to select configurations if the search space becomes too vast.
        # For demonstration purposes, let's limit it to a reasonable number if needed
        # Or, you could remove the hardcoded list altogether.
        # For this example, let's just use the dynamically generated list as is.
        
        logging.info(f"Total configurations to evaluate: {len(configurations)}")

        for config in configurations:
            encoder_name, scaler_name, selector_name, model_name = config
            config_name = f"{model_name}_{encoder_name}_{scaler_name}_{selector_name}"
            
            logging.info(f"\n{'='*50}")
            logging.info(f"Optimizing {config_name}")
            logging.info(f"{'='*50}")
            
            try:
                # Create study
                study = optuna.create_study(
                    direction='maximize',
                    sampler=optuna.samplers.TPESampler(seed=self.random_state),
                    pruner=optuna.pruners.MedianPruner(n_warmup_steps=5)
                )
                
                # Optimize
                study.optimize(
                    lambda trial: self.objective(trial, encoder_name, scaler_name, selector_name, model_name),
                    n_trials=n_trials,
                    timeout=timeout
                )
                
                # Skip if no successful trials
                if not study.best_trial:
                    logging.warning(f"No successful trials for {config_name}")
                    continue
                
                # Train best pipeline
                best_pipeline = self.create_pipeline(encoder_name, scaler_name, selector_name, model_name)
                best_params = self.models[model_name]['params'](study.best_trial)
                best_pipeline.set_params(**best_params)
                best_pipeline.fit(self.X_train, self.y_train)
                
                # Evaluate
                y_pred = best_pipeline.predict(self.X_test)
                # Corrected: Handle multiclass predict_proba for AUC
                if hasattr(best_pipeline.named_steps['classifier'], 'predict_proba'):
                    y_proba = best_pipeline.predict_proba(self.X_test)
                    if self.problem_type == "binary":
                        y_proba_score = y_proba[:, 1]
                    else: # Multiclass
                        y_proba_score = y_proba
                else:
                    y_proba_score = None
                
                # Calculate metrics
                metrics = {
                    'config': config_name,
                    'model': model_name,
                    'encoder': encoder_name,
                    'scaler': scaler_name,
                    'selector': selector_name,
                    'accuracy': accuracy_score(self.y_test, y_pred),
                    'precision': precision_score(self.y_test, y_pred, average='weighted'),
                    'recall': recall_score(self.y_test, y_pred, average='weighted'),
                    'f1': f1_score(self.y_test, y_pred, average='weighted'),
                    'best_params': best_params,
                    'best_pipeline_obj': best_pipeline # Store the trained pipeline object
                }
                
                # Add AUC if available
                if y_proba_score is not None:
                    if self.problem_type == "binary":
                        metrics['auc_roc'] = roc_auc_score(self.y_test, y_proba_score)
                    else: # Multiclass
                        metrics['auc_roc'] = roc_auc_score(self.y_test, y_proba_score, multi_class='ovr')
                elif self.problem_type == "binary":
                    metrics['auc_roc'] = roc_auc_score(self.y_test, y_pred) # Fallback for binary if no predict_proba
                
                self.results.append(metrics)
                logging.info(f"{config_name} | Test AUC: {metrics.get('auc_roc', np.nan):.4f}")
                
                # Store feature importances
                if hasattr(best_pipeline.named_steps['classifier'], 'feature_importances_'):
                    # Accessing feature names correctly after preprocessing
                    # This part can be tricky as ColumnTransformer changes column names
                    # For simplicity, we'll store them for the best model after fitting
                    self.feature_importances_for_plotting = best_pipeline.named_steps['classifier'].feature_importances_
                    
                    # Try to get feature names after preprocessing for more accurate plotting
                    # This is a common challenge with pipelines; for simplicity, we'll use original names + OHE for now
                    preprocessor_fitted = best_pipeline.named_steps['preprocessor']
                    
                    # Get feature names after one-hot encoding if applicable
                    if 'cat' in preprocessor_fitted.named_transformers and hasattr(preprocessor_fitted.named_transformers['cat'].named_steps['encoder'], 'get_feature_names_out'):
                         cat_feature_names = preprocessor_fitted.named_transformers['cat'].named_steps['encoder'].get_feature_names_out(self.categorical_cols)
                    else:
                         cat_feature_names = self.categorical_cols
                    
                    processed_feature_names = self.numerical_cols + list(cat_feature_names) # Combine original numerical and new categorical
                    
                    # If feature selection is applied, you'll need to map importances to selected features
                    if selector_name != 'none':
                        selector = best_pipeline.named_steps['feature_selector']
                        if hasattr(selector, 'get_support'):
                            selected_indices = selector.get_support(indices=True)
                            processed_feature_names = [processed_feature_names[i] for i in selected_indices]
                            
                    self.feature_names_for_plotting = processed_feature_names

                # Visualize optimization
                self._plot_optimization(study, config_name)
                
            except Exception as e:
                logging.error(f"Optimization failed for {config_name}: {str(e)}")
        
        # Finalize results
        if self.results:
            self._finalize_results()
            return True
        return False

    def _plot_optimization(self, study, config_name):
        """Visualize optimization results"""
        try:
            # Optimization history
            fig = plot_optimization_history(study)
            fig.update_layout(title=f"{config_name} Optimization History")
            fig.write_image(f"opt_history_{config_name}.png")
            
            # Parameter importance
            fig = plot_param_importances(study)
            fig.update_layout(title=f"{config_name} Parameter Importance")
            fig.write_image(f"param_importance_{config_name}.png")
            
        except Exception as e:
            logging.error(f"Visualization failed: {str(e)}")

    def _finalize_results(self):
        """Process and store final results"""
        self.results_df = pd.DataFrame(self.results)
        
        # Sort and select best model
        self.results_df = self.results_df.sort_values('auc_roc', ascending=False)
        best_row = self.results_df.iloc[0]
        self.best_model_name = best_row['config']
        # Corrected: Access the stored best_pipeline_obj
        self.best_pipeline = best_row['best_pipeline_obj'] 
        
        logging.info(f"\n{'='*50}")
        logging.info(f"BEST MODEL: {self.best_model_name}")
        logging.info(f"{'='*50}")
        
        # Save results
        self.results_df.drop(columns=['best_pipeline_obj'], inplace=True) # Drop the pipeline object before saving CSV
        self.results_df.to_csv('automl_results.csv', index=False)
        joblib.dump(self.best_pipeline, 'best_model.pkl')
        
        # Plot model comparison
        self.plot_model_comparison()
        
        # Plot feature importances if available
        if hasattr(self, 'feature_importances_for_plotting') and self.feature_importances_for_plotting is not None:
            self.plot_feature_importances()

    def plot_model_comparison(self):
        """Visualize model comparison"""
        plt.figure(figsize=(12, 8))
        sns.barplot(
            x='auc_roc', 
            y='config', 
            data=self.results_df.sort_values('auc_roc', ascending=False),
            palette='viridis'
        )
        plt.title('Model Performance Comparison (AUC-ROC)', fontsize=16)
        plt.xlabel('AUC-ROC Score', fontsize=14)
        plt.ylabel('Configuration', fontsize=14)
        plt.tight_layout()
        plt.savefig('model_performance_comparison.png', dpi=300)
        plt.close()

    def plot_feature_importances(self, top_n=20):
        """Plot top feature importances"""
        if not hasattr(self, 'feature_importances_for_plotting') or self.feature_importances_for_plotting is None:
            logging.warning("Feature importances not available for plotting")
            return
        
        # Get feature names - using the stored names after preprocessing if available
        if hasattr(self, 'feature_names_for_plotting') and self.feature_names_for_plotting:
            feature_names = self.feature_names_for_plotting
        else:
            feature_names = self.numerical_cols + self.categorical_cols # Fallback
            
        # Ensure feature_importances_for_plotting and feature_names have the same length
        if len(feature_names) != len(self.feature_importances_for_plotting):
            logging.warning(f"Mismatch in feature importance array length ({len(self.feature_importances_for_plotting)}) and feature names length ({len(feature_names)}). Cannot plot feature importances correctly.")
            return

        # Create importance DataFrame
        importances = pd.DataFrame({
            'feature': feature_names,
            'importance': self.feature_importances_for_plotting
        }).sort_values('importance', ascending=False).head(top_n)
        
        # Plot
        plt.figure(figsize=(12, 8))
        sns.barplot(x='importance', y='feature', data=importances, palette='rocket')
        plt.title('Top Feature Importances', fontsize=16)
        plt.xlabel('Importance', fontsize=14)
        plt.ylabel('Feature', fontsize=14)
        plt.tight_layout()
        plt.savefig('feature_importances.png', dpi=300)
        plt.close()

    def evaluate(self):
        """Comprehensive evaluation of best model"""
        if not self.best_pipeline:
            logging.error("No best model available for evaluation")
            return None
        
        # Predictions
        y_pred = self.best_pipeline.predict(self.X_test)
        
        # Corrected: Handle multiclass predict_proba for AUC in evaluation
        if hasattr(self.best_pipeline.named_steps['classifier'], 'predict_proba'):
            y_proba = self.best_pipeline.predict_proba(self.X_test)
            if self.problem_type == "binary":
                y_proba_score = y_proba[:, 1]
            else: # Multiclass
                y_proba_score = y_proba
        else:
            y_proba_score = None
            
        # Metrics
        metrics = {
            "accuracy": accuracy_score(self.y_test, y_pred),
            "precision": precision_score(self.y_test, y_pred, average='weighted'),
            "recall": recall_score(self.y_test, y_pred, average='weighted'),
            "f1": f1_score(self.y_test, y_pred, average='weighted'),
            "classification_report": classification_report(self.y_test, y_pred)
        }
        
        # AUC if available
        if y_proba_score is not None:
            if self.problem_type == "binary":
                metrics["auc_roc"] = roc_auc_score(self.y_test, y_proba_score)
            else: # Multiclass
                metrics["auc_roc"] = roc_auc_score(self.y_test, y_proba_score, multi_class='ovr')
        
        # Confusion matrix
        self._plot_confusion_matrix(y_pred)
        
        return metrics

    def _plot_confusion_matrix(self, y_pred):
        """Plot confusion matrix"""
        cm = confusion_matrix(self.y_test, y_pred)
        plt.figure(figsize=(8, 6))
        sns.heatmap(cm, annot=True, fmt='d', cmap='Blues', 
                    xticklabels=['Predicted 0', 'Predicted 1'], # Consider dynamic labels for multiclass
                    yticklabels=['Actual 0', 'Actual 1']) # Consider dynamic labels for multiclass
        plt.title(f'Confusion Matrix: {self.best_model_name}', fontsize=14)
        plt.ylabel('True Label')
        plt.xlabel('Predicted Label')
        plt.tight_layout()
        plt.savefig(f'confusion_matrix_{self.best_model_name}.png', dpi=300)
        plt.close()

# Example usage
if __name__ == "__main__":
    # Load data
    df = pd.read_csv("E:/VS_Code/Projects/Customer_Churn/notebooks/data/processed_customer_churn_data.csv")
    
    # Initialize and run AutoML
    automl = AutoMLTrainer(
        X=df.drop(columns=['customer_status']),
        y=df['customer_status'],
        test_size=0.2,
        random_state=42
    )
    
    # Run optimization
    if automl.optimize(n_trials=20, timeout=600):
        # Evaluate best model
        metrics = automl.evaluate()
        logging.info("\nBest Model Metrics:")
        for k, v in metrics.items():
            if k != "classification_report":
                logging.info(f"{k}: {v:.4f}")
        
        logging.info("\nClassification Report:")
        logging.info(metrics["classification_report"])
    
    logging.info("AutoML process completed")

[2025-07-15 21:46:14,901] 59 root - INFO - Encoded categorical target variable
[2025-07-15 21:46:14,902] 64 root - INFO - Multiclass classification task detected
[2025-07-15 21:46:14,909] 50 root - INFO - Data prepared. Train: (5634, 43), Test: (1409, 43)
[2025-07-15 21:46:14,910] 51 root - INFO - Numerical features: 20, Categorical features: 23
[2025-07-15 21:46:14,911] 199 root - INFO - Components configured: 3 encoders, 3 scalers, 3 feature selectors, 6 models
[2025-07-15 21:46:14,911] 30 root - INFO - AutoML Trainer initialized successfully
[2025-07-15 21:46:14,911] 341 root - INFO - Total configurations to evaluate: 162
[2025-07-15 21:46:14,911] 347 root - INFO - 
[2025-07-15 21:46:14,912] 348 root - INFO - Optimizing LogisticRegression_onehot_standard_variance
[2025-07-15 21:46:14,912] 349 root - INFO - ==================================================
[I 2025-07-15 21:46:14,913] A new study created in memory with name: no-name-d350389c-e39b-462b-807d-edf7170d802e
[2025-07-15 21

[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.002057 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2348
[LightGBM] [Info] Number of data points in the train set: 5634, number of used features: 77
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further spli

e:\VS_Code\Projects\Customer_Churn\venv\Lib\site-packages\sklearn\utils\validation.py:2749: UserWarning:

X does not have valid feature names, but LGBMClassifier was fitted with feature names

e:\VS_Code\Projects\Customer_Churn\venv\Lib\site-packages\sklearn\utils\validation.py:2749: UserWarning:

X does not have valid feature names, but LGBMClassifier was fitted with feature names

[2025-07-15 21:46:21,339] 414 root - INFO - LightGBM_onehot_standard_variance | Test AUC: 1.0000
[2025-07-15 21:46:21,340] 448 root - ERROR - Optimization failed for LightGBM_onehot_standard_variance: 'ColumnTransformer' object has no attribute 'named_transformers'
[2025-07-15 21:46:21,340] 347 root - INFO - 
[2025-07-15 21:46:21,341] 348 root - INFO - Optimizing LogisticRegression_onehot_standard_mutual_info
[2025-07-15 21:46:21,341] 349 root - INFO - ==================================================
[I 2025-07-15 21:46:21,342] A new study created in memory with name: no-name-912093d2-fd0c-4989-91ca-68561

[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.002021 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 2384
[LightGBM] [Info] Number of data points in the train set: 5634, number of used features: 95
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

e:\VS_Code\Projects\Customer_Churn\venv\Lib\site-packages\sklearn\utils\validation.py:2749: UserWarning:

X does not have valid feature names, but LGBMClassifier was fitted with feature names

e:\VS_Code\Projects\Customer_Churn\venv\Lib\site-packages\sklearn\utils\validation.py:2749: UserWarning:

X does not have valid feature names, but LGBMClassifier was fitted with feature names

[2025-07-15 21:54:35,462] 414 root - INFO - LightGBM_onehot_standard_mutual_info | Test AUC: 1.0000
[2025-07-15 21:54:35,463] 448 root - ERROR - Optimization failed for LightGBM_onehot_standard_mutual_info: 'ColumnTransformer' object has no attribute 'named_transformers'
[2025-07-15 21:54:35,463] 347 root - INFO - 
[2025-07-15 21:54:35,464] 348 root - INFO - Optimizing LogisticRegression_onehot_standard_none
[2025-07-15 21:54:35,464] 349 root - INFO - ==================================================
[I 2025-07-15 21:54:35,465] A new study created in memory with name: no-name-077bcc70-5a7e-46d5-af86-e8e1fd

...

[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.001299 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 7309
[LightGBM] [Info] Number of data points in the train set: 5634, number of used features: 40
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

e:\VS_Code\Projects\Customer_Churn\venv\Lib\site-packages\sklearn\utils\validation.py:2749: UserWarning:

X does not have valid feature names, but LGBMClassifier was fitted with feature names

e:\VS_Code\Projects\Customer_Churn\venv\Lib\site-packages\sklearn\utils\validation.py:2749: UserWarning:

X does not have valid feature names, but LGBMClassifier was fitted with feature names

[2025-07-15 22:29:35,398] 414 root - INFO - LightGBM_catboost_none_mutual_info | Test AUC: 0.9473
[2025-07-15 22:29:35,399] 448 root - ERROR - Optimization failed for LightGBM_catboost_none_mutual_info: 'ColumnTransformer' object has no attribute 'named_transformers'
[2025-07-15 22:29:35,401] 347 root - INFO - 
[2025-07-15 22:29:35,402] 348 root - INFO - Optimizing LogisticRegression_catboost_none_none
[2025-07-15 22:29:35,403] 349 root - INFO - ==================================================
[I 2025-07-15 22:29:35,405] A new study created in memory with name: no-name-4a790daf-49b2-4b98-beaa-a8158422556c

[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.001285 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 7309
[LightGBM] [Info] Number of data points in the train set: 5634, number of used features: 40
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

e:\VS_Code\Projects\Customer_Churn\venv\Lib\site-packages\sklearn\utils\validation.py:2749: UserWarning:

X does not have valid feature names, but LGBMClassifier was fitted with feature names

e:\VS_Code\Projects\Customer_Churn\venv\Lib\site-packages\sklearn\utils\validation.py:2749: UserWarning:

X does not have valid feature names, but LGBMClassifier was fitted with feature names

[2025-07-15 22:29:49,741] 414 root - INFO - LightGBM_catboost_none_none | Test AUC: 0.9473
[2025-07-15 22:29:49,742] 448 root - ERROR - Optimization failed for LightGBM_catboost_none_none: 'ColumnTransformer' object has no attribute 'named_transformers'
[2025-07-15 22:29:49,746] 483 root - INFO - 
[2025-07-15 22:29:49,747] 484 root - INFO - BEST MODEL: RandomForest_onehot_standard_variance
[2025-07-15 22:29:49,747] 485 root - INFO - ==================================================
C:\Users\Nihal\AppData\Local\Temp\ipykernel_8768\452099144.py:502: FutureWarning:



Passing `palette` without assigning `hue`

ValueError: X has 6809 features, but VarianceThreshold is expecting 43 features as input.

In [10]:
all_model_results_df = pd.read_csv('automl_results.csv')
all_model_results_df

config         model   encoder    scaler  \
0  RandomForest_onehot_minmax_mutual_info  RandomForest    onehot    minmax   
1             CatBoost_catboost_none_none      CatBoost  catboost      none   
2        XGBoost_target_standard_variance       XGBoost    target  standard   

      selector  accuracy  precision    recall        f1  \
0  mutual_info  0.979418   0.981345  0.979418  0.979906   
1         none  0.838893   0.844584  0.838893  0.840470   
2     variance  0.734564   0.557034  0.734564  0.630050   

                                         best_params   auc_roc  
0  {'classifier__n_estimators': 250, 'classifier_...  0.997513  
1  {'classifier__iterations': 687, 'classifier__l...  0.948663  
2  {'classifier__n_estimators': 250, 'classifier_...  0.793307

In [12]:
# Top 5 models by AUC-ROC
all_model_results_df.sort_values(by='auc_roc', ascending=False).head()

config         model   encoder    scaler  \
0  RandomForest_onehot_minmax_mutual_info  RandomForest    onehot    minmax   
1             CatBoost_catboost_none_none      CatBoost  catboost      none   
2        XGBoost_target_standard_variance       XGBoost    target  standard   

      selector  accuracy  precision    recall        f1  \
0  mutual_info  0.979418   0.981345  0.979418  0.979906   
1         none  0.838893   0.844584  0.838893  0.840470   
2     variance  0.734564   0.557034  0.734564  0.630050   

                                         best_params   auc_roc  
0  {'classifier__n_estimators': 250, 'classifier_...  0.997513  
1  {'classifier__iterations': 687, 'classifier__l...  0.948663  
2  {'classifier__n_estimators': 250, 'classifier_...  0.793307

In [13]:
# Results for XGBoost models
all_model_results_df[all_model_results_df['model'] == 'XGBoost']

config    model encoder    scaler  selector  \
2  XGBoost_target_standard_variance  XGBoost  target  standard  variance   

   accuracy  precision    recall       f1  \
2  0.734564   0.557034  0.734564  0.63005   

                                         best_params   auc_roc  
2  {'classifier__n_estimators': 250, 'classifier_...  0.793307

In [14]:
if hasattr(automl, 'feature_importances_for_plotting') and automl.feature_importances_for_plotting is not None:
    feature_importances = automl.feature_importances_for_plotting
    feature_names = automl.feature_names_for_plotting # This will be the processed names

    if feature_names and len(feature_names) == len(feature_importances):
        importance_df = pd.DataFrame({
            'feature': feature_names,
            'importance': feature_importances
        }).sort_values('importance', ascending=False)

        print("\nRaw Feature Importances DataFrame:")
        print(importance_df.head(20)) # Print top 20 for example

        # You can also regenerate the plot with custom settings if needed
        plt.figure(figsize=(12, 8))
        sns.barplot(x='importance', y='feature', data=importance_df.head(20), palette='viridis')
        plt.title('Custom Top Feature Importances Plot', fontsize=16)
        plt.xlabel('Importance', fontsize=14)
        plt.ylabel('Feature', fontsize=14)
        plt.tight_layout()
        plt.show()
    else:
        print("Feature names or importances are not correctly available for custom plotting.")
else:
    print("Feature importances were not calculated or stored for the best model.")

AttributeError: 'AutoMLTrainer' object has no attribute 'feature_names_for_plotting'

In [124]:
pipe = trainer.create_pipeline('onehot', 'LogisticRegression')
pipe.set_params(**{
    'classifier__C': 1.0,
    'classifier__solver': 'lbfgs'
})
pipe.fit(trainer.x_train, trainer.y_train)
print(pipe.score(trainer.x_test, trainer.y_test))

0.9907735982966643
